# word task

In [44]:
import pandas as pd
import logging
import re
import sqlite3

class word_operator:
    """
    This class takes care of work operations - 
    load word data from file, word count, count by alphabet, word filter with cleaning, loading data to sqlite
    """
    def __init__(self):
        """
        All dataset is loaded and db table is created.
        """
        try:
            logging.basicConfig(filename='word.log', encoding='utf-8', level=logging.DEBUG)

            self.data1 = pd.read_fwf('resource/vocab.enron.txt', sep='\n', header=None)
            self.list_data = list(self.data1.values.flatten())
            self.list_data_1 = list(self.data1.values.flatten())

            self.data2 = pd.read_fwf('resource/vocab.kos.txt', sep='\n', header=None)   
            self.list_data_2 = list(self.data2.values.flatten())
            self.list_data.extend(self.list_data_2)

            self.data3 = pd.read_fwf('resource/vocab.nips.txt', sep='\n', header=None)
            self.list_data_3 = list(self.data3.values.flatten())
            self.list_data.extend(self.list_data_3)


            self.data4 = pd.read_fwf('resource/vocab.nytimes.txt', sep='\n', header=None)   
            self.list_data_4 = list(self.data4.values.flatten())
            self.list_data.extend(self.list_data_4)    

            self.data5 = pd.read_fwf('resource/vocab.pubmed.txt', sep='\n', header=None)   
            self.list_data_5 = list(self.data5.values.flatten())
            self.list_data.extend(self.list_data_5)    

            self.wordcount = {}
            
            self.alphacount = {
                'a' : 0, 'b' : 0, 'c': 0, 'd' : 0, 'e' : 0, 'f' : 0, 'g' : 0, 'h' : 0, 'i' : 0, 'j' : 0,
                'k' : 0, 'l' : 0, 'm' : 0, 'n' : 0, 'o' : 0, 'p' : 0, 'q' : 0, 'r' : 0, 's' : 0, 't' : 0,
                'u' : 0, 'v' : 0, 'w' : 0, 'x' : 0, 'y' : 0, 'z' : 0,
                
                'A' : 0, 'B' : 0, 'C': 0, 'D' : 0, 'E' : 0, 'F' : 0, 'G' : 0, 'H' : 0, 'I' : 0, 'J' : 0,
                'K' : 0, 'L' : 0, 'M' : 0, 'N' : 0, 'O' : 0, 'P' : 0, 'Q' : 0, 'R' : 0, 'S' : 0, 'T' : 0,
                'U' : 0, 'V' : 0, 'W' : 0, 'X' : 0, 'Y' : 0, 'Z' : 0
            }
            
            db = sqlite3.connect("word.db")
            cur = db.cursor()
            cur.execute('create table word_table(vocab_1 text, vocab_2 text, vocab_3 text, vocab_4 text, vocab_5 text)')
            db.commit()
            db.close()
            
        except Exception as e:
            logging.error(e)
            
    def count_by_repeativewords(self):
        """
         q1 = try to find out a count of each 
                 and every word in a respective file return a list of tuple with word and its respective count 
        """
        try:
            for i in self.list_data:            
                if self.wordcount.get(i):
                    self.wordcount[i] += 1
                else:
                    self.wordcount[i] = 1
        except Exception as e:
            logging.error(e)
        return list(self.wordcount.items())
            
    def count_by_alpha(self):
        """
         q2 = try to perform a reduce operation to get a count of all the word starting with same alphabet
                sample examle = [(a,56) , (b,34),...........]
        """
        try:
            for i in self.alphacount:
                self.alphacount[i] = len(list(filter(lambda x : type(x) == str and x.startswith(i), self.list_data)))
        except Exception as e:
            logging.error(e)
        return list(self.alphacount.items())
    
    def filter_words(self):
        """
        q3 = Try to filter out all the words from dataset . 
            .001.abstract = abstract
            =.002 = delete
        """
        new_list = []
        #print(self.list_data)
        try:
            new_list = list(map(lambda x : re.search(r"([a-z]{2,})", x).group(1),
                                list(filter(lambda x : type(x) == str 
                                            and re.search(r"([a-z]{2,})", x) != None, self.list_data))))
        except Exception as e:
            logging.error(e)
        return new_list
    
    def store_in_db(self):
        """
        q4 = create a tuple set of all the records avaialble in all the five file and then store it in sqllite DB . 
            (aah,>=,354,fdsf,wer)
        """
        db = None
        data_count = 0
        try:
            db = sqlite3.connect("word.db")
            cur = db.cursor()
            
            data = list(zip(self.list_data_1,self.list_data_2,self.list_data_3,self.list_data_4, self.list_data_5))
            
            for i in data:
                insert_stmt = f"insert into word_table values{str(i)}"
                logging.debug(insert_stmt)
                cur.execute(insert_stmt)
            db.commit()
            data_count = cur.execute("select count(*) from word_table").fetchone()
        except Exception as e:
            logging.error(e)
        finally:
            if db != None:
                db.close()
        return data_count
                    
if __name__ == "__main__":
    w = word_operator()
    print(w.count_by_repeativewords())
    print(w.count_by_alpha())
    #print(len(w.list_data))
    print(w.filter_words())
    #print(len(w.filter_words()))
    print(w.store_in_db())

   
    

[('aaa', 3), ('aaas', 2), ('aactive', 1), ('aadvantage', 1), ('aaker', 1), ('aap', 2), ('aapg', 1), ('aaron', 2), ('aarp', 2), ('aas', 2), ('aau', 2), ('ab1890', 1), ('ab1x', 1), ('ab31x', 1), ('aba', 2), ('abacus', 2), ('abag', 1), ('abalone', 3), ('abandon', 4), ('abandoned', 4), ('abandoning', 4), ('abandonment', 4), ('abate', 3), ('abated', 3), ('abb', 3), ('abbott', 3), ('abbreviated', 4), ('abbreviation', 3), ('abby', 1), ('abc', 4), ('abcm', 1), ('abdullah', 2), ('abe', 3), ('abel', 2), ('aberdeen', 2), ('abernathy', 1), ('aberration', 3), ('abeyance', 2), ('abhay', 1), ('abhyankar', 1), ('abide', 3), ('abilene', 1), ('abilities', 4), ('ability', 5), ('abitibi', 1), ('able', 4), ('abn', 2), ('abnamro', 1), ('abnormal', 4), ('aboard', 4), ('abolish', 3), ('abolished', 3), ('abolishing', 3), ('abortion', 4), ('abound', 4), ('aboutface', 1), ('aboveaverage', 1), ('abovemarket', 1), ('abovereferenced', 1), ('abraham', 4), ('abramson', 1), ('abreast', 3), ('abroad', 4), ('abrogate', 

[('a', 16458), ('b', 10452), ('c', 21314), ('d', 12324), ('e', 10017), ('f', 8372), ('g', 7084), ('h', 9589), ('i', 9936), ('j', 1568), ('k', 2422), ('l', 7797), ('m', 14241), ('n', 9119), ('o', 5623), ('p', 20149), ('q', 937), ('r', 11618), ('s', 20717), ('t', 11522), ('u', 4519), ('v', 3814), ('w', 3768), ('x', 473), ('y', 602), ('z', 58840), ('A', 0), ('B', 0), ('C', 0), ('D', 0), ('E', 0), ('F', 0), ('G', 0), ('H', 0), ('I', 0), ('J', 0), ('K', 0), ('L', 0), ('M', 0), ('N', 0), ('O', 0), ('P', 0), ('Q', 0), ('R', 0), ('S', 0), ('T', 0), ('U', 0), ('V', 0), ('W', 0), ('X', 0), ('Y', 0), ('Z', 0)]
['aaa', 'aaas', 'aactive', 'aadvantage', 'aaker', 'aap', 'aapg', 'aaron', 'aarp', 'aas', 'aau', 'ab', 'ab', 'ab', 'aba', 'abacus', 'abag', 'abalone', 'abandon', 'abandoned', 'abandoning', 'abandonment', 'abate', 'abated', 'abb', 'abbott', 'abbreviated', 'abbreviation', 'abby', 'abc', 'abcm', 'abdullah', 'abe', 'abel', 'aberdeen', 'abernathy', 'aberration', 'abeyance', 'abhay', 'abhyankar', 

(6906,)
